In [21]:
import pandas as pd
import numpy as np
import re
import openpyxl 
from datetime import datetime
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go

init_notebook_mode(connected=True)

In [5]:
def names_to_months(x):
    a = re.sub("\D", "", x)[:4]
    if len(a) > 0:
        a = a[:4]
    elif x == "*":
        a = 'install'
    else:
        a = x
    return a

def remove_bottom(df):
    for i in range(df.shape[0]):
        for j in range(df.shape[1]):
            if j < i:
                df.iat[i,j] = np.nan
    return df

def fill_diag(m, v):
    for i in range(m.shape[0]):
        for j in range(m.shape[1]):
            if j == i:
                m.iat[i,j] = v[i]
    return m

def change_matrix_orientation(m):
    m = m.transpose()
    m = m[m.columns[::-1]]
    n = m.shape[0]
    for i in range(n):
        for j in range(i+1):
            if j != j+n-1-i:
                m.iat[i,j] = m.iat[i,j+n-1-i]
                m.iat[i,j+n-1-i] = np.nan
    m.columns = range(n)
    return m

In [6]:
def culc_mau(df_mau):
    m_mau_reg = df_mau.pivot_table(index='created per month', columns='active month', values='users', aggfunc=sum).fillna(0).applymap(float)
    m_mau = m_mau_reg.drop(['install'], axis = 1)
    m_mau = remove_bottom(m_mau)
    m_mau = fill_diag(m_mau, m_mau_reg['install'])
    m_mau.index = m_mau.index.map(lambda x: datetime.strptime(x, "%Y-%m-%d %H:%M:%S").strftime('%Y-%m-%d'))
    return m_mau

def culc_regs(m_mau):
    m_regs = pd.DataFrame(np.diagonal(m_mau), columns=['installs'])
    m_regs.index = months
    return m_regs

def culc_payers(df_payers):
    m_payers_reg = df_payers.pivot_table(index='created per month', columns='active month', values='users', aggfunc=sum).fillna(0).applymap(float)
    m_payers = m_payers_reg.drop(['install'], axis = 1)
    m_payers = remove_bottom(m_payers)
    m_payers.index = m_payers.index.map(lambda x: datetime.strptime(x, "%Y-%m-%d %H:%M:%S").strftime('%Y-%m-%d'))
    return m_payers

def culc_revenue(df_revenue):
    df = df_revenue.groupby(['created per month']).sum()
    m_revenue = remove_bottom(df)
    m_revenue.index = m_revenue.index.map(lambda x: datetime.strptime(x, "%Y-%m-%d %H:%M:%S").strftime('%Y-%m-%d'))
    return m_revenue

In [7]:
# mau with registrations
# notref https://portraits.core.tf/app/kibana#/visualize/create?type=histogram&indexPattern=portraits&_g=(refreshInterval:(display:Off,pause:!f,value:0),time:(from:now-15m,mode:quick,to:now))&_a=(filters:!(),linked:!f,query:(query_string:(analyze_wildcard:!t,query:'created:%5B%222015-01-01T00:00:00%22%20TO%202018-02-28T23:59:59%5D%20AND%20referral:0')),uiState:(spy:(mode:(fill:!f,name:table))),vis:(aggs:!((id:'1',params:(),schema:metric,type:count),(id:'2',params:(filters:!(('$$hashKey':'object:2113',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topfacemobappandroid'))),label:''),('$$hashKey':'object:2123',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topfacemobappios')))),('$$hashKey':'object:2128',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:standalonetf')))),('$$hashKey':'object:2133',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:vk')))),('$$hashKey':'object:2138',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:ok')))),('$$hashKey':'object:2143',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:fb')))))),schema:segment,type:filters),(id:'4',params:(filters:!(('$$hashKey':'object:8412',input:(query:(query_string:(analyze_wildcard:!t,query:'*'))),label:''),('$$hashKey':'object:8421',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1501.topfacemobappandroid%20OR%20user_mau.1501.topfacemobappios%20OR%20user_mau.1501.topface%20OR%20user_mau.1501.standalonetf)')))),('$$hashKey':'object:8425',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1502.topfacemobappandroid%20OR%20user_mau.1502.topfacemobappios%20OR%20user_mau.1502.topface%20OR%20user_mau.1502.standalonetf)')))),('$$hashKey':'object:8431',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1503.topfacemobappandroid%20OR%20user_mau.1503.topfacemobappios%20OR%20user_mau.1503.topface%20OR%20user_mau.1503.standalonetf)')))),('$$hashKey':'object:4826',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1504.topfacemobappandroid%20OR%20user_mau.1504.topfacemobappios%20OR%20user_mau.1504.topface%20OR%20user_mau.1504.standalonetf)')))),('$$hashKey':'object:4839',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1505.topfacemobappandroid%20OR%20user_mau.1505.topfacemobappios%20OR%20user_mau.1505.topface%20OR%20user_mau.1505.standalonetf)')))),('$$hashKey':'object:4844',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1506.topfacemobappandroid%20OR%20user_mau.1506.topfacemobappios%20OR%20user_mau.1506.topface%20OR%20user_mau.1506.standalonetf)')))),('$$hashKey':'object:4849',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1507.topfacemobappandroid%20OR%20user_mau.1507.topfacemobappios%20OR%20user_mau.1507.topface%20OR%20user_mau.1507.standalonetf)')))),('$$hashKey':'object:4854',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1508.topfacemobappandroid%20OR%20user_mau.1508.topfacemobappios%20OR%20user_mau.1508.topface%20OR%20user_mau.1508.standalonetf)')))),('$$hashKey':'object:4859',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1509.topfacemobappandroid%20OR%20user_mau.1509.topfacemobappios%20OR%20user_mau.1509.topface%20OR%20user_mau.1509.standalonetf)')))),('$$hashKey':'object:4864',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1510.topfacemobappandroid%20OR%20user_mau.1510.topfacemobappios%20OR%20user_mau.1510.topface%20OR%20user_mau.1510.standalonetf)')))),('$$hashKey':'object:4869',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1511.topfacemobappandroid%20OR%20user_mau.1511.topfacemobappios%20OR%20user_mau.1511.topface%20OR%20user_mau.1511.standalonetf)')))),('$$hashKey':'object:4874',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1512.topfacemobappandroid%20OR%20user_mau.1512.topfacemobappios%20OR%20user_mau.1512.topface%20OR%20user_mau.1512.standalonetf)')))),('$$hashKey':'object:4879',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1601.topfacemobappandroid%20OR%20user_mau.1601.topfacemobappios%20OR%20user_mau.1601.topface%20OR%20user_mau.1601.standalonetf)')))),('$$hashKey':'object:4884',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1602.topfacemobappandroid%20OR%20user_mau.1602.topfacemobappios%20OR%20user_mau.1602.topface%20OR%20user_mau.1602.standalonetf)')))),('$$hashKey':'object:4889',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1603.topfacemobappandroid%20OR%20user_mau.1603.topfacemobappios%20OR%20user_mau.1603.topface%20OR%20user_mau.1603.standalonetf)')))),('$$hashKey':'object:4894',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1604.topfacemobappandroid%20OR%20user_mau.1604.topfacemobappios%20OR%20user_mau.1604.topface%20OR%20user_mau.1604.standalonetf)')))),('$$hashKey':'object:4899',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1605.topfacemobappandroid%20OR%20user_mau.1605.topfacemobappios%20OR%20user_mau.1605.topface%20OR%20user_mau.1605.standalonetf)')))),('$$hashKey':'object:4904',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1606.topfacemobappandroid%20OR%20user_mau.1606.topfacemobappios%20OR%20user_mau.1606.topface%20OR%20user_mau.1606.standalonetf)')))),('$$hashKey':'object:4909',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1607.topfacemobappandroid%20OR%20user_mau.1607.topfacemobappios%20OR%20user_mau.1607.topface%20OR%20user_mau.1607.standalonetf)')))),('$$hashKey':'object:4922',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1608.topfacemobappandroid%20OR%20user_mau.1608.topfacemobappios%20OR%20user_mau.1608.topface%20OR%20user_mau.1608.standalonetf)')))),('$$hashKey':'object:4927',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1609.topfacemobappandroid%20OR%20user_mau.1609.topfacemobappios%20OR%20user_mau.1609.topface%20OR%20user_mau.1609.standalonetf)')))),('$$hashKey':'object:4932',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1610.topfacemobappandroid%20OR%20user_mau.1610.topfacemobappios%20OR%20user_mau.1610.topface%20OR%20user_mau.1610.standalonetf)')))),('$$hashKey':'object:4937',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1611.topfacemobappandroid%20OR%20user_mau.1611.topfacemobappios%20OR%20user_mau.1611.topface%20OR%20user_mau.1611.standalonetf)')))),('$$hashKey':'object:4942',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1612.topfacemobappandroid%20OR%20user_mau.1612.topfacemobappios%20OR%20user_mau.1612.topface%20OR%20user_mau.1612.standalonetf)')))),('$$hashKey':'object:4947',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1701.topfacemobappandroid%20OR%20user_mau.1701.topfacemobappios%20OR%20user_mau.1701.topface%20OR%20user_mau.1701.standalonetf)')))),('$$hashKey':'object:4952',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1702.topfacemobappandroid%20OR%20user_mau.1702.topfacemobappios%20OR%20user_mau.1702.topface%20OR%20user_mau.1702.standalonetf)')))),('$$hashKey':'object:4957',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1703.topfacemobappandroid%20OR%20user_mau.1703.topfacemobappios%20OR%20user_mau.1703.topface%20OR%20user_mau.1703.standalonetf)')))),('$$hashKey':'object:4962',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1704.topfacemobappandroid%20OR%20user_mau.1704.topfacemobappios%20OR%20user_mau.1704.topface%20OR%20user_mau.1704.standalonetf)')))),('$$hashKey':'object:4967',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1705.topfacemobappandroid%20OR%20user_mau.1705.topfacemobappios%20OR%20user_mau.1705.topface%20OR%20user_mau.1705.standalonetf)')))),('$$hashKey':'object:4972',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1706.topfacemobappandroid%20OR%20user_mau.1706.topfacemobappios%20OR%20user_mau.1706.topface%20OR%20user_mau.1706.standalonetf)')))),('$$hashKey':'object:4985',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1707.topfacemobappandroid%20OR%20user_mau.1707.topfacemobappios%20OR%20user_mau.1707.topface%20OR%20user_mau.1707.standalonetf)')))),('$$hashKey':'object:4990',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1708.topfacemobappandroid%20OR%20user_mau.1708.topfacemobappios%20OR%20user_mau.1708.topface%20OR%20user_mau.1708.standalonetf)')))),('$$hashKey':'object:4995',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1709.topfacemobappandroid%20OR%20user_mau.1709.topfacemobappios%20OR%20user_mau.1709.topface%20OR%20user_mau.1709.standalonetf)')))),('$$hashKey':'object:5000',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1710.topfacemobappandroid%20OR%20user_mau.1710.topfacemobappios%20OR%20user_mau.1710.topface%20OR%20user_mau.1710.standalonetf)')))),('$$hashKey':'object:5005',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1711.topfacemobappandroid%20OR%20user_mau.1711.topfacemobappios%20OR%20user_mau.1711.topface%20OR%20user_mau.1711.standalonetf)')))),('$$hashKey':'object:3579',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1712.topfacemobappandroid%20OR%20user_mau.1712.topfacemobappios%20OR%20user_mau.1712.topface%20OR%20user_mau.1712.standalonetf)')))),('$$hashKey':'object:3584',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1801.topfacemobappandroid%20OR%20user_mau.1801.topfacemobappios%20OR%20user_mau.1801.topface%20OR%20user_mau.1801.standalonetf)')))),('$$hashKey':'object:3589',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1802.topfacemobappandroid%20OR%20user_mau.1802.topfacemobappios%20OR%20user_mau.1802.topface%20OR%20user_mau.1802.standalonetf)'))))),row:!t),schema:split,type:filters),(id:'5',params:(customInterval:'2h',extended_bounds:(),field:created,interval:M,min_doc_count:1),schema:group,type:date_histogram)),listeners:(),params:(addLegend:!t,addTimeMarker:!f,addTooltip:!t,defaultYExtents:!f,mode:stacked,scale:linear,setYExtents:!f,shareYAxis:!t,times:!(),yAxis:()),title:'New%20Visualization',type:histogram))
# ref    https://portraits.core.tf/app/kibana#/visualize/create?type=histogram&indexPattern=portraits&_g=(refreshInterval:(display:Off,pause:!f,value:0),time:(from:now-15m,mode:quick,to:now))&_a=(filters:!(),linked:!f,query:(query_string:(analyze_wildcard:!t,query:'created:%5B%222015-01-01T00:00:00%22%20TO%202018-02-28T23:59:59%5D%20AND%20referral:1')),uiState:(spy:(mode:(fill:!f,name:table))),vis:(aggs:!((id:'1',params:(),schema:metric,type:count),(id:'5',params:(customInterval:'2h',extended_bounds:(),field:created,interval:M,min_doc_count:1),schema:group,type:date_histogram),(id:'2',params:(filters:!(('$$hashKey':'object:2113',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topfacemobappandroid'))),label:''),('$$hashKey':'object:2123',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topfacemobappios')))),('$$hashKey':'object:2128',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:standalonetf')))),('$$hashKey':'object:2133',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:vk')))),('$$hashKey':'object:2138',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:ok')))),('$$hashKey':'object:2143',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:fb')))))),schema:segment,type:filters),(id:'4',params:(filters:!(('$$hashKey':'object:8412',input:(query:(query_string:(analyze_wildcard:!t,query:'*'))),label:''),('$$hashKey':'object:8421',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1501.topfacemobappandroid%20OR%20user_mau.1501.topfacemobappios%20OR%20user_mau.1501.topface%20OR%20user_mau.1501.standalonetf)')))),('$$hashKey':'object:8425',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1502.topfacemobappandroid%20OR%20user_mau.1502.topfacemobappios%20OR%20user_mau.1502.topface%20OR%20user_mau.1502.standalonetf)')))),('$$hashKey':'object:8431',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1503.topfacemobappandroid%20OR%20user_mau.1503.topfacemobappios%20OR%20user_mau.1503.topface%20OR%20user_mau.1503.standalonetf)')))),('$$hashKey':'object:4826',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1504.topfacemobappandroid%20OR%20user_mau.1504.topfacemobappios%20OR%20user_mau.1504.topface%20OR%20user_mau.1504.standalonetf)')))),('$$hashKey':'object:4839',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1505.topfacemobappandroid%20OR%20user_mau.1505.topfacemobappios%20OR%20user_mau.1505.topface%20OR%20user_mau.1505.standalonetf)')))),('$$hashKey':'object:4844',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1506.topfacemobappandroid%20OR%20user_mau.1506.topfacemobappios%20OR%20user_mau.1506.topface%20OR%20user_mau.1506.standalonetf)')))),('$$hashKey':'object:4849',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1507.topfacemobappandroid%20OR%20user_mau.1507.topfacemobappios%20OR%20user_mau.1507.topface%20OR%20user_mau.1507.standalonetf)')))),('$$hashKey':'object:4854',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1508.topfacemobappandroid%20OR%20user_mau.1508.topfacemobappios%20OR%20user_mau.1508.topface%20OR%20user_mau.1508.standalonetf)')))),('$$hashKey':'object:4859',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1509.topfacemobappandroid%20OR%20user_mau.1509.topfacemobappios%20OR%20user_mau.1509.topface%20OR%20user_mau.1509.standalonetf)')))),('$$hashKey':'object:4864',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1510.topfacemobappandroid%20OR%20user_mau.1510.topfacemobappios%20OR%20user_mau.1510.topface%20OR%20user_mau.1510.standalonetf)')))),('$$hashKey':'object:4869',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1511.topfacemobappandroid%20OR%20user_mau.1511.topfacemobappios%20OR%20user_mau.1511.topface%20OR%20user_mau.1511.standalonetf)')))),('$$hashKey':'object:4874',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1512.topfacemobappandroid%20OR%20user_mau.1512.topfacemobappios%20OR%20user_mau.1512.topface%20OR%20user_mau.1512.standalonetf)')))),('$$hashKey':'object:4879',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1601.topfacemobappandroid%20OR%20user_mau.1601.topfacemobappios%20OR%20user_mau.1601.topface%20OR%20user_mau.1601.standalonetf)')))),('$$hashKey':'object:4884',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1602.topfacemobappandroid%20OR%20user_mau.1602.topfacemobappios%20OR%20user_mau.1602.topface%20OR%20user_mau.1602.standalonetf)')))),('$$hashKey':'object:4889',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1603.topfacemobappandroid%20OR%20user_mau.1603.topfacemobappios%20OR%20user_mau.1603.topface%20OR%20user_mau.1603.standalonetf)')))),('$$hashKey':'object:4894',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1604.topfacemobappandroid%20OR%20user_mau.1604.topfacemobappios%20OR%20user_mau.1604.topface%20OR%20user_mau.1604.standalonetf)')))),('$$hashKey':'object:4899',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1605.topfacemobappandroid%20OR%20user_mau.1605.topfacemobappios%20OR%20user_mau.1605.topface%20OR%20user_mau.1605.standalonetf)')))),('$$hashKey':'object:4904',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1606.topfacemobappandroid%20OR%20user_mau.1606.topfacemobappios%20OR%20user_mau.1606.topface%20OR%20user_mau.1606.standalonetf)')))),('$$hashKey':'object:4909',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1607.topfacemobappandroid%20OR%20user_mau.1607.topfacemobappios%20OR%20user_mau.1607.topface%20OR%20user_mau.1607.standalonetf)')))),('$$hashKey':'object:4922',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1608.topfacemobappandroid%20OR%20user_mau.1608.topfacemobappios%20OR%20user_mau.1608.topface%20OR%20user_mau.1608.standalonetf)')))),('$$hashKey':'object:4927',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1609.topfacemobappandroid%20OR%20user_mau.1609.topfacemobappios%20OR%20user_mau.1609.topface%20OR%20user_mau.1609.standalonetf)')))),('$$hashKey':'object:4932',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1610.topfacemobappandroid%20OR%20user_mau.1610.topfacemobappios%20OR%20user_mau.1610.topface%20OR%20user_mau.1610.standalonetf)')))),('$$hashKey':'object:4937',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1611.topfacemobappandroid%20OR%20user_mau.1611.topfacemobappios%20OR%20user_mau.1611.topface%20OR%20user_mau.1611.standalonetf)')))),('$$hashKey':'object:4942',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1612.topfacemobappandroid%20OR%20user_mau.1612.topfacemobappios%20OR%20user_mau.1612.topface%20OR%20user_mau.1612.standalonetf)')))),('$$hashKey':'object:4947',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1701.topfacemobappandroid%20OR%20user_mau.1701.topfacemobappios%20OR%20user_mau.1701.topface%20OR%20user_mau.1701.standalonetf)')))),('$$hashKey':'object:4952',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1702.topfacemobappandroid%20OR%20user_mau.1702.topfacemobappios%20OR%20user_mau.1702.topface%20OR%20user_mau.1702.standalonetf)')))),('$$hashKey':'object:4957',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1703.topfacemobappandroid%20OR%20user_mau.1703.topfacemobappios%20OR%20user_mau.1703.topface%20OR%20user_mau.1703.standalonetf)')))),('$$hashKey':'object:4962',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1704.topfacemobappandroid%20OR%20user_mau.1704.topfacemobappios%20OR%20user_mau.1704.topface%20OR%20user_mau.1704.standalonetf)')))),('$$hashKey':'object:4967',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1705.topfacemobappandroid%20OR%20user_mau.1705.topfacemobappios%20OR%20user_mau.1705.topface%20OR%20user_mau.1705.standalonetf)')))),('$$hashKey':'object:4972',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1706.topfacemobappandroid%20OR%20user_mau.1706.topfacemobappios%20OR%20user_mau.1706.topface%20OR%20user_mau.1706.standalonetf)')))),('$$hashKey':'object:4985',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1707.topfacemobappandroid%20OR%20user_mau.1707.topfacemobappios%20OR%20user_mau.1707.topface%20OR%20user_mau.1707.standalonetf)')))),('$$hashKey':'object:4990',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1708.topfacemobappandroid%20OR%20user_mau.1708.topfacemobappios%20OR%20user_mau.1708.topface%20OR%20user_mau.1708.standalonetf)')))),('$$hashKey':'object:4995',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1709.topfacemobappandroid%20OR%20user_mau.1709.topfacemobappios%20OR%20user_mau.1709.topface%20OR%20user_mau.1709.standalonetf)')))),('$$hashKey':'object:5000',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1710.topfacemobappandroid%20OR%20user_mau.1710.topfacemobappios%20OR%20user_mau.1710.topface%20OR%20user_mau.1710.standalonetf)')))),('$$hashKey':'object:5005',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1711.topfacemobappandroid%20OR%20user_mau.1711.topfacemobappios%20OR%20user_mau.1711.topface%20OR%20user_mau.1711.standalonetf)')))),('$$hashKey':'object:3579',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1712.topfacemobappandroid%20OR%20user_mau.1712.topfacemobappios%20OR%20user_mau.1712.topface%20OR%20user_mau.1712.standalonetf)')))),('$$hashKey':'object:3584',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1801.topfacemobappandroid%20OR%20user_mau.1801.topfacemobappios%20OR%20user_mau.1801.topface%20OR%20user_mau.1801.standalonetf)')))),('$$hashKey':'object:3589',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:(user_mau.1802.topfacemobappandroid%20OR%20user_mau.1802.topfacemobappios%20OR%20user_mau.1802.topface%20OR%20user_mau.1802.standalonetf)'))))),row:!t),schema:split,type:filters)),listeners:(),params:(addLegend:!t,addTimeMarker:!f,addTooltip:!t,defaultYExtents:!f,mode:stacked,scale:linear,setYExtents:!f,shareYAxis:!t,times:!(),yAxis:()),title:'New%20Visualization',type:histogram))

# paying part
# notref https://portraits.core.tf/app/kibana#/visualize/create?type=histogram&indexPattern=portraits&_g=(refreshInterval:(display:Off,pause:!f,value:0),time:(from:now-15m,mode:quick,to:now))&_a=(filters:!(),linked:!f,query:(query_string:(analyze_wildcard:!t,query:'created:%5B%222015-01-01T00:00:00%22%20TO%202018-02-28T23:59:59%5D%20AND%20referral:0')),uiState:(spy:(mode:(fill:!f,name:!n))),vis:(aggs:!((id:'1',params:(),schema:metric,type:count),(id:'5',params:(customInterval:'2h',extended_bounds:(),field:created,interval:M,min_doc_count:1),schema:group,type:date_histogram),(id:'2',params:(filters:!(('$$hashKey':'object:2113',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topfacemobappandroid'))),label:''),('$$hashKey':'object:2123',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topfacemobappios')))),('$$hashKey':'object:2128',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:standalonetf')))),('$$hashKey':'object:2133',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:vk')))),('$$hashKey':'object:2138',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:ok')))),('$$hashKey':'object:2143',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:fb')))))),schema:segment,type:filters),(id:'4',params:(filters:!(('$$hashKey':'object:8412',input:(query:(query_string:(analyze_wildcard:!t,query:'*'))),label:''),('$$hashKey':'object:8421',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1501.total')))),('$$hashKey':'object:8425',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1502.total')))),('$$hashKey':'object:8431',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1503.total')))),('$$hashKey':'object:4826',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1504.total')))),('$$hashKey':'object:4839',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1505.total')))),('$$hashKey':'object:4844',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1506.total')))),('$$hashKey':'object:4849',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1507.total')))),('$$hashKey':'object:4854',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1508.total')))),('$$hashKey':'object:4859',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1509.total')))),('$$hashKey':'object:4864',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1510.total')))),('$$hashKey':'object:4869',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1511.total')))),('$$hashKey':'object:4874',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1512.total')))),('$$hashKey':'object:4879',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1601.total')))),('$$hashKey':'object:4884',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1602.total')))),('$$hashKey':'object:4889',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1603.total')))),('$$hashKey':'object:4894',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1604.total')))),('$$hashKey':'object:4899',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1605.total')))),('$$hashKey':'object:4904',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1606.total')))),('$$hashKey':'object:4909',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1607.total')))),('$$hashKey':'object:4922',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1608.total')))),('$$hashKey':'object:4927',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1609.total')))),('$$hashKey':'object:4932',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1610.total')))),('$$hashKey':'object:4937',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1611.total')))),('$$hashKey':'object:4942',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1612.total')))),('$$hashKey':'object:4947',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1701.total')))),('$$hashKey':'object:4952',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1702.total')))),('$$hashKey':'object:4957',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1703.total')))),('$$hashKey':'object:4962',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1704.total')))),('$$hashKey':'object:4967',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1705.total')))),('$$hashKey':'object:4972',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1706.total')))),('$$hashKey':'object:4985',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1707.total')))),('$$hashKey':'object:4990',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1708.total')))),('$$hashKey':'object:4995',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1709.total')))),('$$hashKey':'object:5000',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1710.total')))),('$$hashKey':'object:5005',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1711.total')))),('$$hashKey':'object:3579',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1712.total')))),('$$hashKey':'object:3584',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1801.total')))),('$$hashKey':'object:3589',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1802.total'))))),row:!t),schema:split,type:filters)),listeners:(),params:(addLegend:!t,addTimeMarker:!f,addTooltip:!t,defaultYExtents:!f,mode:stacked,scale:linear,setYExtents:!f,shareYAxis:!t,times:!(),yAxis:()),title:'New%20Visualization',type:histogram))
# ref    https://portraits.core.tf/app/kibana#/visualize/create?type=histogram&indexPattern=portraits&_g=(refreshInterval:(display:Off,pause:!f,value:0),time:(from:now-15m,mode:quick,to:now))&_a=(filters:!(),linked:!f,query:(query_string:(analyze_wildcard:!t,query:'created:%5B%222015-01-01T00:00:00%22%20TO%202018-02-28T23:59:59%5D%20AND%20referral:1')),uiState:(spy:(mode:(fill:!f,name:!n))),vis:(aggs:!((id:'1',params:(),schema:metric,type:count),(id:'5',params:(customInterval:'2h',extended_bounds:(),field:created,interval:M,min_doc_count:1),schema:group,type:date_histogram),(id:'2',params:(filters:!(('$$hashKey':'object:2113',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topfacemobappandroid'))),label:''),('$$hashKey':'object:2123',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topfacemobappios')))),('$$hashKey':'object:2128',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:standalonetf')))),('$$hashKey':'object:2133',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:vk')))),('$$hashKey':'object:2138',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:ok')))),('$$hashKey':'object:2143',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:fb')))))),schema:segment,type:filters),(id:'4',params:(filters:!(('$$hashKey':'object:8412',input:(query:(query_string:(analyze_wildcard:!t,query:'*'))),label:''),('$$hashKey':'object:8421',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1501.total')))),('$$hashKey':'object:8425',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1502.total')))),('$$hashKey':'object:8431',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1503.total')))),('$$hashKey':'object:4826',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1504.total')))),('$$hashKey':'object:4839',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1505.total')))),('$$hashKey':'object:4844',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1506.total')))),('$$hashKey':'object:4849',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1507.total')))),('$$hashKey':'object:4854',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1508.total')))),('$$hashKey':'object:4859',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1509.total')))),('$$hashKey':'object:4864',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1510.total')))),('$$hashKey':'object:4869',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1511.total')))),('$$hashKey':'object:4874',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1512.total')))),('$$hashKey':'object:4879',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1601.total')))),('$$hashKey':'object:4884',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1602.total')))),('$$hashKey':'object:4889',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1603.total')))),('$$hashKey':'object:4894',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1604.total')))),('$$hashKey':'object:4899',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1605.total')))),('$$hashKey':'object:4904',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1606.total')))),('$$hashKey':'object:4909',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1607.total')))),('$$hashKey':'object:4922',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1608.total')))),('$$hashKey':'object:4927',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1609.total')))),('$$hashKey':'object:4932',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1610.total')))),('$$hashKey':'object:4937',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1611.total')))),('$$hashKey':'object:4942',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1612.total')))),('$$hashKey':'object:4947',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1701.total')))),('$$hashKey':'object:4952',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1702.total')))),('$$hashKey':'object:4957',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1703.total')))),('$$hashKey':'object:4962',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1704.total')))),('$$hashKey':'object:4967',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1705.total')))),('$$hashKey':'object:4972',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1706.total')))),('$$hashKey':'object:4985',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1707.total')))),('$$hashKey':'object:4990',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1708.total')))),('$$hashKey':'object:4995',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1709.total')))),('$$hashKey':'object:5000',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1710.total')))),('$$hashKey':'object:5005',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1711.total')))),('$$hashKey':'object:3579',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1712.total')))),('$$hashKey':'object:3584',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1801.total')))),('$$hashKey':'object:3589',input:(query:(query_string:(analyze_wildcard:!t,query:'_exists_:revenue_in_month.1802.total'))))),row:!t),schema:split,type:filters)),listeners:(),params:(addLegend:!t,addTimeMarker:!f,addTooltip:!t,defaultYExtents:!f,mode:stacked,scale:linear,setYExtents:!f,shareYAxis:!t,times:!(),yAxis:()),title:'New%20Visualization',type:histogram))
    
# revenue
# revenue 1501 - 1607 total		https://portraits.core.tf/app/kibana#/visualize/create?type=histogram&indexPattern=portraits&_g=(refreshInterval:(display:Off,pause:!f,value:0),time:(from:now-15m,mode:quick,to:now))&_a=(filters:!(),linked:!f,query:(query_string:(analyze_wildcard:!t,query:'created:%5B%222015-01-01T00:00:00%22%20TO%20%222018-02-28T23:59:59%22%5D')),uiState:(spy:(mode:(fill:!f,name:table))),vis:(aggs:!((id:'1',params:(field:revenue_in_month.1501.total),schema:metric,type:sum),(id:'2',params:(field:revenue_in_month.1502.total),schema:metric,type:sum),(id:'3',params:(field:revenue_in_month.1503.total),schema:metric,type:sum),(id:'4',params:(field:revenue_in_month.1504.total),schema:metric,type:sum),(id:'5',params:(field:revenue_in_month.1505.total),schema:metric,type:sum),(id:'6',params:(field:revenue_in_month.1506.total),schema:metric,type:sum),(id:'21',params:(filters:!(('$$hashKey':'object:3820',input:(query:(query_string:(analyze_wildcard:!t,query:'referral:0'))),label:''),('$$hashKey':'object:3829',input:(query:(query_string:(analyze_wildcard:!t,query:'referral:1'))))),row:!t),schema:split,type:filters),(id:'20',params:(filters:!(('$$hashKey':'object:3756',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topfacemobappandroid'))),label:''),('$$hashKey':'object:3765',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topfacemobappios')))),('$$hashKey':'object:3770',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:standalonetf')))),('$$hashKey':'object:3775',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:vk')))),('$$hashKey':'object:3780',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:ok')))),('$$hashKey':'object:3785',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:fb')))))),schema:group,type:filters),(id:'19',params:(customInterval:'2h',extended_bounds:(),field:created,interval:M,min_doc_count:1),schema:segment,type:date_histogram),(id:'22',params:(field:revenue_in_month.1507.total),schema:metric,type:sum),(id:'23',params:(field:revenue_in_month.1508.total),schema:metric,type:sum),(id:'24',params:(field:revenue_in_month.1509.total),schema:metric,type:sum),(id:'25',params:(field:revenue_in_month.1510.total),schema:metric,type:sum),(id:'26',params:(field:revenue_in_month.1511.total),schema:metric,type:sum),(id:'27',params:(field:revenue_in_month.1512.total),schema:metric,type:sum),(id:'28',params:(field:revenue_in_month.1601.total),schema:metric,type:sum),(id:'29',params:(field:revenue_in_month.1602.total),schema:metric,type:sum),(id:'30',params:(field:revenue_in_month.1603.total),schema:metric,type:sum),(id:'31',params:(field:revenue_in_month.1604.total),schema:metric,type:sum),(id:'32',params:(field:revenue_in_month.1605.total),schema:metric,type:sum),(id:'33',params:(field:revenue_in_month.1606.total),schema:metric,type:sum),(id:'34',params:(field:revenue_in_month.1607.total),schema:metric,type:sum)),listeners:(),params:(addLegend:!t,addTimeMarker:!f,addTooltip:!t,defaultYExtents:!f,mode:stacked,scale:linear,setYExtents:!f,shareYAxis:!t,times:!(),yAxis:()),title:'New%20Visualization',type:histogram))
# revenue 1608 - 1802 total		https://portraits.core.tf/app/kibana#/visualize/create?type=histogram&indexPattern=portraits&_g=(refreshInterval:(display:Off,pause:!f,value:0),time:(from:now-15m,mode:quick,to:now))&_a=(filters:!(),linked:!f,query:(query_string:(analyze_wildcard:!t,query:'created:%5B%222015-01-01T00:00:00%22%20TO%20%222018-02-28T23:59:59%22%5D')),uiState:(spy:(mode:(fill:!f,name:table))),vis:(aggs:!((id:'21',params:(filters:!(('$$hashKey':'object:3820',input:(query:(query_string:(analyze_wildcard:!t,query:'referral:0'))),label:''),('$$hashKey':'object:3829',input:(query:(query_string:(analyze_wildcard:!t,query:'referral:1'))))),row:!t),schema:split,type:filters),(id:'20',params:(filters:!(('$$hashKey':'object:3756',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topfacemobappandroid'))),label:''),('$$hashKey':'object:3765',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topfacemobappios')))),('$$hashKey':'object:3770',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:standalonetf')))),('$$hashKey':'object:3775',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:vk')))),('$$hashKey':'object:3780',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:ok')))),('$$hashKey':'object:3785',input:(query:(query_string:(analyze_wildcard:!t,query:'first_app:topface%20AND%20platform:fb')))))),schema:group,type:filters),(id:'19',params:(customInterval:'2h',extended_bounds:(),field:created,interval:M,min_doc_count:1),schema:segment,type:date_histogram),(id:'35',params:(field:revenue_in_month.1608.total),schema:metric,type:sum),(id:'36',params:(field:revenue_in_month.1609.total),schema:metric,type:sum),(id:'37',params:(field:revenue_in_month.1610.total),schema:metric,type:sum),(id:'38',params:(field:revenue_in_month.1611.total),schema:metric,type:sum),(id:'39',params:(field:revenue_in_month.1612.total),schema:metric,type:sum),(id:'40',params:(field:revenue_in_month.1701.total),schema:metric,type:sum),(id:'41',params:(field:revenue_in_month.1702.total),schema:metric,type:sum),(id:'42',params:(field:revenue_in_month.1703.total),schema:metric,type:sum),(id:'43',params:(field:revenue_in_month.1704.total),schema:metric,type:sum),(id:'44',params:(field:revenue_in_month.1705.total),schema:metric,type:sum),(id:'45',params:(field:revenue_in_month.1706.total),schema:metric,type:sum),(id:'46',params:(field:revenue_in_month.1707.total),schema:metric,type:sum),(id:'47',params:(field:revenue_in_month.1708.total),schema:metric,type:sum),(id:'48',params:(field:revenue_in_month.1709.total),schema:metric,type:sum),(id:'49',params:(field:revenue_in_month.1710.total),schema:metric,type:sum),(id:'50',params:(field:revenue_in_month.1711.total),schema:metric,type:sum),(id:'51',params:(field:revenue_in_month.1712.total),schema:metric,type:sum),(id:'52',params:(field:revenue_in_month.1801.total),schema:metric,type:sum),(id:'53',params:(field:revenue_in_month.1802.total),schema:metric,type:sum)),listeners:(),params:(addLegend:!t,addTimeMarker:!f,addTooltip:!t,defaultYExtents:!f,mode:stacked,scale:linear,setYExtents:!f,shareYAxis:!t,times:!(),yAxis:()),title:'New%20Visualization',type:histogram))

In [14]:
df_ref_mau = pd.read_csv(r'C:\Users\isaco\Downloads\cohort analysis\data\ref_mau.csv',thousands=',')
df_notref_mau = pd.read_csv(r'C:\Users\isaco\Downloads\cohort analysis\data\notref_mau.csv',thousands=',') 
df_ref_mau['ref'] = 'ref'
df_notref_mau['ref'] = 'notref'
df_mau = df_notref_mau.append(df_ref_mau)
df_mau.columns = ['created per month', 'app', 'active month', 'users', 'ref']
df_mau = df_mau[df_mau['created per month'] < '2018-03-01 00:00:00']
df_mau['active month'] = df_mau['active month'].map(lambda x: names_to_months(x))

In [15]:
df_revenue = pd.read_csv(r'C:\Users\isaco\Downloads\cohort analysis\data\revenue_1.csv',thousands=',').append(pd.read_csv(r'C:\Users\isaco\Downloads\cohort analysis\data\revenue_2.csv',thousands=','))
df_revenue.rename(columns={'filters': 'ref', 'filters.1': 'app'}, inplace=True)
df_revenue = df_revenue[df_revenue['created per month'] < '2018-03-01 00:00:00']
df_revenue.columns = df_revenue.columns.map(lambda x: names_to_months(x))
df_revenue = df_revenue.fillna(0)

In [16]:
df_ref_payers = pd.read_csv(r'C:\Users\isaco\Downloads\cohort analysis\data\ref_payers.csv',thousands=',')
df_notref_payers = pd.read_csv(r'C:\Users\isaco\Downloads\cohort analysis\data\notref_payers.csv',thousands=',')
df_ref_payers['ref'] = 'ref'
df_notref_payers['ref'] = 'notref'
df_payers = df_notref_payers.append(df_ref_payers)
df_payers.columns = ['created per month', 'app', 'active month', 'users', 'ref']
df_payers = df_payers[df_payers['created per month'] < '2018-03-01 00:00:00']
df_payers['active month'] = df_payers['active month'].map(lambda x: re.sub("\D", "", x)[:4] if len(x) > 1 else 'install')

In [17]:
dict_app = {'first_app:topfacemobappandroid': 'android','first_app:topfacemobappios':'ios','first_app:standalonetf':'st',
            'first_app:topface AND platform:vk' : 'vk', 'first_app:topface AND platform:ok': 'ok','first_app:topface AND platform:fb': 'fb'}
dict_ref = {'referral:0': 'notref','referral:1':'ref'}
df_mau['app'] = df_mau['app'].map(dict_app)
df_payers['app'] = df_payers['app'].map(dict_app)
df_revenue['app'] = df_revenue['app'].map(dict_app)
df_revenue['ref'] = df_revenue['ref'].map(dict_ref)

In [18]:
months = sorted(set(df_mau['created per month'].map(lambda x: datetime.strptime(x, "%Y-%m-%d %H:%M:%S").strftime('%Y-%m-%d'))))
apps = list(set(df_mau['app']))
refs = list(set(df_mau['ref']))
variable_list = ['regs','mau','payers','revenue','retention','payers_part','arpu_monthly','arppu_monthly','ltv_equal','ltv_cumsum']

In [23]:
drop_menus = []
data_mau = []
data_regs = []
data_payers = []
data_revenue = []
data_retention = []
data_payers_part = []
data_arpu_monthly = []
data_arppu_monthly = []
data_ltv_equal = []
data_ltv_cumsum = []

drop_menus_mau = []
drop_menus_regs = []
drop_menus_payers = []
drop_menus_revenue = []
drop_menus_retention = []
drop_menus_payers_part = []
drop_menus_arpu_monthly = []
drop_menus_arppu_monthly = []
drop_menus_ltv_equal = []
drop_menus_ltv_cumsum = []
i = 0
for ref in refs:
    for app in apps:
        m_mau = culc_mau(df_mau[(df_mau['app'] == app) & (df_mau['ref'] == ref)])
        m_regs = culc_regs(m_mau)
        m_payers = culc_payers(df_payers[(df_payers['app'] == app) & (df_payers['ref'] == ref)])
        m_revenue = culc_revenue(df_revenue[(df_revenue['app'] == app) & (df_revenue['ref'] == ref)])
        m_retention = m_mau.divide(m_regs['installs'], axis='index')
        m_payers_part = m_payers.divide(m_mau)
        m_arpu_monthly = m_revenue.divide(m_mau)
        m_arppu_monthly = m_revenue.divide(m_payers)
        m_ltv_equal = m_revenue.divide(m_regs['installs'], axis='index')
        m_ltv_cumsum = np.cumsum(m_ltv_equal, axis=1)
        
        writer = pd.ExcelWriter(r'C:\Users\isaco\Downloads\cohort analysis\data'+'\cohort_analysis' + '_' + ref + '_' + app + '.xlsx')
        for variable in variable_list:
            i += 1
            if variable == 'regs':
                m = round(vars()['m_' + variable], 0)
                m.to_excel(writer,variable)        # записываем в эксель
                heatmap = go.Heatmap(              # делаем визуализацию, тип графика - Heatmap
                    z = m.values,
                    x = m.index.values,
                    y = m.columns,
                    name = ref + '_' + app+ '_' + variable,
                )
                data_regs.append(heatmap)
                drop_menus_regs.append(
                    dict(
                    #args=['visible', [False]*2*i + [True]*2 + [False]*2*(120-1-i)],
                    label= ref + ' ' + app+ ' ' + variable,
                    method='restyle'
                    )
                )
            elif variable == 'mau':
                m = round(change_matrix_orientation(vars()['m_' + variable]), 0)
                m.to_excel(writer,variable)        # записываем в эксель
                heatmap = go.Heatmap(              # делаем визуализацию, тип графика - Heatmap
                    z = m.values,
                    x = m.index.values,
                    y = m.columns,
                    name = ref + '_' + app+ '_' + variable,
                )
                data_mau.append(heatmap)
                drop_menus_mau.append(
                    dict(
                    #args=['visible', [False]*2*i + [True]*2 + [False]*2*(120-1-i)],
                    label= ref + ' ' + app+ ' ' + variable,
                    method='restyle'
                    )
                )
            elif variable == 'payers':
                m = round(change_matrix_orientation(vars()['m_' + variable]), 0)
                m.to_excel(writer,variable)        # записываем в эксель
                heatmap = go.Heatmap(              # делаем визуализацию, тип графика - Heatmap
                    z = m.values,
                    x = m.index.values,
                    y = m.columns,
                    name = ref + '_' + app+ '_' + variable,
                )
                data_payers.append(heatmap)
                drop_menus_payers.append(
                    dict(
                    #args=['visible', [False]*2*i + [True]*2 + [False]*2*(120-1-i)],
                    label= ref + ' ' + app+ ' ' + variable,
                    method='restyle'
                    )
                )
            elif variable == 'revenue':
                m = round(change_matrix_orientation(vars()['m_' + variable]), 0)
                m.to_excel(writer,variable)        # записываем в эксель
                heatmap = go.Heatmap(              # делаем визуализацию, тип графика - Heatmap
                    z = m.values,
                    x = m.index.values,
                    y = m.columns,
                    name = ref + '_' + app+ '_' + variable,
                )
                data_revenue.append(heatmap)
                drop_menus_revenue.append(
                    dict(
                    #args=['visible', [False]*2*i + [True]*2 + [False]*2*(120-1-i)],
                    label= ref + ' ' + app+ ' ' + variable,
                    method='restyle'
                    )
                )
            elif variable == 'retention':
                m = round(change_matrix_orientation(vars()['m_' + variable]) * 100, 2)
                m.to_excel(writer,variable)        # записываем в эксель
                heatmap = go.Heatmap(              # делаем визуализацию, тип графика - Heatmap
                    z = m.values,
                    x = m.index.values,
                    y = m.columns,
                    name = ref + '_' + app+ '_' + variable,
                )
                data_retention.append(heatmap)
                drop_menus_retention.append(
                    dict(
                    #args=['visible', [False]*2*i + [True]*2 + [False]*2*(120-1-i)],
                    label= ref + ' ' + app+ ' ' + variable,
                    method='restyle'
                    )
                )
            elif variable == 'payers_part':
                m = round(change_matrix_orientation(vars()['m_' + variable]) * 100, 2)
                m.to_excel(writer,variable)        # записываем в эксель
                heatmap = go.Heatmap(              # делаем визуализацию, тип графика - Heatmap
                    z = m.values,
                    x = m.index.values,
                    y = m.columns,
                    name = ref + '_' + app+ '_' + variable,
                )
                data_payers_part.append(heatmap)
                drop_menus_payers_part.append(
                    dict(
                    #args=['visible', [False]*2*i + [True]*2 + [False]*2*(120-1-i)],
                    label= ref + ' ' + app+ ' ' + variable,
                    method='restyle'
                    )
                )
            elif variable == 'arpu_monthly':
                m = round(change_matrix_orientation(vars()['m_' + variable]), 4)
                m.to_excel(writer,variable)        # записываем в эксель
                heatmap = go.Heatmap(              # делаем визуализацию, тип графика - Heatmap
                    z = m.values,
                    x = m.index.values,
                    y = m.columns,
                    name = ref + '_' + app+ '_' + variable,
                )
                data_arpu_monthly.append(heatmap)
                drop_menus_arpu_monthly.append(
                    dict(
                    #args=['visible', [False]*2*i + [True]*2 + [False]*2*(120-1-i)],
                    label= ref + ' ' + app+ ' ' + variable,
                    method='restyle'
                    )
                )
            elif variable == 'arppu_monthly':
                m = round(change_matrix_orientation(vars()['m_' + variable]), 4)
                m.to_excel(writer,variable)        # записываем в эксель
                heatmap = go.Heatmap(              # делаем визуализацию, тип графика - Heatmap
                    z = m.values,
                    x = m.index.values,
                    y = m.columns,
                    name = ref + '_' + app+ '_' + variable,
                )
                data_arppu_monthly.append(heatmap)
                drop_menus_arppu_monthly.append(
                    dict(
                    #args=['visible', [False]*2*i + [True]*2 + [False]*2*(120-1-i)],
                    label= ref + ' ' + app+ ' ' + variable,
                    method='restyle'
                    )
                )
            elif variable == 'ltv_equal':
                m = round(change_matrix_orientation(vars()['m_' + variable]), 4)
                m.to_excel(writer,variable)        # записываем в эксель
                heatmap = go.Heatmap(              # делаем визуализацию, тип графика - Heatmap
                    z = m.values,
                    x = m.index.values,
                    y = m.columns,
                    name = ref + '_' + app+ '_' + variable,
                )
                data_ltv_equal.append(heatmap)
                drop_menus_ltv_equal.append(
                    dict(
                    #args=['visible', [False]*2*i + [True]*2 + [False]*2*(120-1-i)],
                    label= ref + ' ' + app+ ' ' + variable,
                    method='restyle'
                    )
                )
            elif variable == 'ltv_cumsum':
                m = round(change_matrix_orientation(vars()['m_' + variable]), 4)
                m.to_excel(writer,variable)        # записываем в эксель
                heatmap = go.Heatmap(              # делаем визуализацию, тип графика - Heatmap
                    z = m.values,
                    x = m.index.values,
                    y = m.columns,
                    name = ref + '_' + app+ '_' + variable,
                )
                data_ltv_cumsum.append(heatmap)
                drop_menus_ltv_cumsum.append(
                    dict(
                    #args=['visible', [False]*2*i + [True]*2 + [False]*2*(120-1-i)],
                    label= ref + ' ' + app+ ' ' + variable,
                    method='restyle'
                    )
                )
            workbook  = writer.book               #создаем условное форматирование в эксель
            worksheet = writer.sheets[variable]
            #worksheet.conditional_format('B2:AM39', {'type': '3_color_scale'})        
        writer.save()
        
            
        
        # print(ref, app, m_mau.shape[0], m_regs.shape[0], m_payers.shape[0], m_revenue.shape[0], m_retention.shape[0], m_payers_part.shape[0], m_arpu_monthly.shape[0], m_arppu_monthly.shape[0],m_ltv_equal.shape[0], m_ltv_cumsum.shape[0])
     
        #writer = pd.ExcelWriter('./out/cohort_analysis' + '_' + ref + '_' + app + '.xlsx')
        #for variable in variable_list:
        #     vars()['m_' + variable].to_excel(writer,variable)
        #writer.save()
        
        #for variable in variable_list:
        #     vars()['m_' + variable +'_' + ref + '_' + app] = vars()['m_' + variable]
        #writer.save()

In [28]:
data = [data_mau ,data_regs ,data_payers ,data_revenue ,data_retention ,data_payers_part,\
        data_arpu_monthly,data_arppu_monthly,data_ltv_equal,data_ltv_cumsum]
drop_menus = [drop_menus_mau ,drop_menus_regs ,drop_menus_payers, drop_menus_revenue,   drop_menus_retention, \
drop_menus_payers_part, drop_menus_arpu_monthly, drop_menus_arppu_monthly, drop_menus_ltv_equal ,drop_menus_ltv_cumsum]

In [29]:
for i in range (10):    
    layout = go.Layout(
        title='Когортный анализ',
        updatemenus=list([
            dict(
                x = -0.1,
                y = 1,
                yanchor = 'top',
                buttons = drop_menus[i]
            ),
        ]),
        autosize=False,
        width=700,
        height=700
    )    
    fig = go.Figure(data = data[i], layout = layout)
    iplot(fig)

In [1]:
vars()['m_' + variable]

NameError: name 'variable' is not defined